In [4]:
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.datasets import cifar10

from wandb.keras import WandbMetricsLogger, WandbModelCheckpoint
import pickle
import data_pre_processing
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3' 
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import wandb
from wandb.keras import WandbCallback
from wandb.keras import WandbMetricsLogger, WandbModelCheckpoint

import self_har_models
tf.get_logger().setLevel('INFO')

In [5]:
wandb.login()

wandb: Currently logged in as: blyt1. Use `wandb login --relogin` to force relogin


True

In [7]:
# get data from pickle 
with open('pickled_datasets/pamap.pickle', 'rb') as file:
    pamap_df = pickle.load(file)
with open('pickled_datasets/hhar.pickle', 'rb') as file:
    hhar_df = pickle.load(file)
with open('pickled_datasets/motionsense.pickle', 'rb') as file:
    motion_sense_df = pickle.load(file)
    
def concat_datasets(datasets, sensor_type):
    concated_datasets = {}
    ##TODO need to check key to see whether mag exists
    for df in datasets:
        concated_datasets.update(df[sensor_type])
    return concated_datasets

cdf = concat_datasets([pamap_df, hhar_df, motion_sense_df], "acc")
def get_labels(data):
    all_labels = []
    for user in data:
        all_labels = np.concatenate((np.unique(data[user][0][1]), all_labels))
    labels = np.unique(all_labels)
    return labels

labels = get_labels(cdf)
label_map = {label: index for index, label in enumerate(labels)}
print(label_map)
user_datasets_processed = data_pre_processing.pre_process_dataset_composite(
    cdf, label_map, 6, 
    ['101', '102', '103', '104', '105', '106', '107', 'a', 'b', 'c', 'd', 'e', 'f', 'g', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '20'], 
    ["108", "109", "h", "i", "21", "22", "23", "24"], 400, 200
)

# implement early stopping
callback = tf.keras.callbacks.EarlyStopping(patience=3, restore_best_weights=True)

{'IMU ankle': 0, 'IMU chest': 1, 'IMU hand': 2, 'Phone': 3, 'Watch': 4, 'iphone': 5}
getting mean
[-0.18597652  1.40292431  4.05411898]
[6.31367612 5.0870368  5.47022979]
normalising train set
normalisnig test


In [8]:
sweep_config = {
  'method': 'grid', 
  'metric': {
      'name': 'epoch/val_loss',
      'goal': 'minimize'
  },
  'early_terminate':{
      'type': 'hyperband',
      'min_iter': 5
  },
  'parameters': {
      'batch_size': {
          'values': [32, 64, 128, 256]
      },
      'dropout1': {
          'values': [0.3, 0.4, 0.5]
        },
      'dropout2': {
          'values': [0.3, 0.4, 0.5]
        },
      'layer1': {
          'values': [32, 64, 128, 256, 512]
      },
      'layer2': {
          'values': [32, 64, 128, 256, 512]
      },
      'dense1': {
          'values': [50, 100, 150, 200, 250, 300]
      },
      'dense2': {
          'values': [50, 100, 150, 200, 250]
      }
  }
}



In [9]:
sweep_id = wandb.sweep(sweep_config, project="sweep4")

Create sweep with ID: qgbqyy1y
Sweep URL: https://wandb.ai/blyt1/sweep4/sweeps/qgbqyy1y


In [10]:
def sweep_train(config_defaults=None):
    wandb.init(project="sweep4")
    # an initial value
    configs = {
        'layer1': 128,
        'layer2': 64,
        'dropout1': 0.3,
        'dropout2': 0.3,
        'dense1': 50,
        'dense2': 50
    }

    # Specify the other hyperparameters to the configuration
    config = wandb.config
    config.epochs = 5



    inputs = tf.keras.Input(shape=(400,3), name='input')
    x = inputs
    x = tf.keras.layers.Dense(wandb.config.dense1, activation='relu')(x)
    x = tf.keras.layers.Conv1D(
            wandb.config.layer1, 3,
            activation='relu',
            strides = 1,
            kernel_regularizer=tf.keras.regularizers.l2(l=1e-4)
        )(x)
    x = tf.keras.layers.Conv1D(
            wandb.config.layer2, 3,
            activation='relu',
            strides = 1,
            kernel_regularizer=tf.keras.regularizers.l2(l=1e-4),
        )(x)
    x = tf.keras.layers.MaxPool1D(pool_size=4, padding='valid', data_format='channels_last', strides=2)(x)

    x = tf.keras.layers.Conv1D(
        32, 5,
        activation='relu',
        strides = 2,
        kernel_regularizer=tf.keras.regularizers.l2(l=1e-4),
        )(x)
    x = tf.keras.layers.Conv1D(
        32, 5,
        activation='relu',
        strides = 2,
        kernel_regularizer=tf.keras.regularizers.l2(l=1e-4),
        )(x)
    x = tf.keras.layers.MaxPool1D(pool_size=4, padding='valid', data_format='channels_last', strides=2)(x)

    x = tf.keras.layers.Dropout(wandb.config.dropout1)(x)
    x = tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(96))(x)
    x = tf.keras.layers.Dropout(wandb.config.dropout2)(x)
    # x = tf.keras.layers.Dense(96, activation='relu')(x)
    x = tf.keras.layers.Dense(wandb.config.dense2, activation='softmax')(x)

    CNNLSTN_model = tf.keras.Model(inputs, x, name="CNN-LSTM")
    full_CNNLSTM_model = self_har_models.attach_full_har_classification_head(CNNLSTN_model, 6, optimizer=tf.keras.optimizers.legacy.Adam(learning_rate=0.0001))


    wandb.config.architecture_name = "CNN-LSTM"


    # Prepare the metrics.
    train_acc_metric = keras.metrics.SparseCategoricalAccuracy()
    val_acc_metric = keras.metrics.SparseCategoricalAccuracy()
    
    full_CNNLSTM_model.fit(user_datasets_processed[0][0], user_datasets_processed[0][1]
                    , epochs=100, validation_data=(user_datasets_processed[1][0], user_datasets_processed[1][1]), callbacks=[callback, WandbMetricsLogger(log_freq=5),
                      WandbModelCheckpoint("models")])

In [32]:
wandb.finish()

In [ ]:
wandb.agent(sweep_id, function=sweep_train, count=100)

wandb: Agent Starting Run: bk1f8sps with config:
wandb: 	batch_size: 32
wandb: 	dense1: 50
wandb: 	dense2: 50
wandb: 	dropout1: 0.3
wandb: 	dropout2: 0.3
wandb: 	layer1: 32
wandb: 	layer2: 32
wandb: WARNING Ignored wandb.init() arg project when running a sweep.


2023-11-18 15:31:25.454613: I tensorflow/core/common_runtime/executor.cc:1209] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'gradients/split_2_grad/concat/split_2/split_dim' with dtype int32
	 [[{{node gradients/split_2_grad/concat/split_2/split_dim}}]]
2023-11-18 15:31:25.457617: I tensorflow/core/common_runtime/executor.cc:1209] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'gradients/split_grad/concat/split/split_dim' with dtype int32
	 [[{{node gradients/split_grad/concat/split/split_dim}}]]
2023-11-18 15:31:25.459463: I tensorflow/core/common_runtime/executor.cc:1209] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You mus

Epoch 1/100


2023-11-18 15:31:27.230832: I tensorflow/core/common_runtime/executor.cc:1209] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'gradients/split_2_grad/concat/split_2/split_dim' with dtype int32
	 [[{{node gradients/split_2_grad/concat/split_2/split_dim}}]]
2023-11-18 15:31:27.233413: I tensorflow/core/common_runtime/executor.cc:1209] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'gradients/split_grad/concat/split/split_dim' with dtype int32
	 [[{{node gradients/split_grad/concat/split/split_dim}}]]
2023-11-18 15:31:27.235065: I tensorflow/core/common_runtime/executor.cc:1209] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You mus

2499/2499 [==============================] - ETA: 0s - loss: 0.6674 - categorical_accuracy: 0.7305 - auc: 0.9574 - precision: 0.8480 - recall: 0.5942

...

2499/2499 [==============================] - 34s 14ms/step - loss: 0.0893 - categorical_accuracy: 0.9767 - auc: 0.9987 - precision: 0.9781 - recall: 0.9753 - val_loss: 0.0815 - val_categorical_accuracy: 0.9789 - val_auc: 0.9989 - val_precision: 0.9801 - val_recall: 0.9779
Epoch 15/100
2494/2499 [============================>.] - ETA: 0s - loss: 0.0869 - categorical_accuracy: 0.9770 - auc: 0.9988 - precision: 0.9783 - recall: 0.9756

2023-11-18 16:04:20.159797: I tensorflow/core/common_runtime/executor.cc:1209] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'gradients/split_2_grad/concat/split_2/split_dim' with dtype int32
	 [[{{node gradients/split_2_grad/concat/split_2/split_dim}}]]
2023-11-18 16:04:20.162182: I tensorflow/core/common_runtime/executor.cc:1209] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You must feed a value for placeholder tensor 'gradients/split_grad/concat/split/split_dim' with dtype int32
	 [[{{node gradients/split_grad/concat/split/split_dim}}]]
2023-11-18 16:04:20.163913: I tensorflow/core/common_runtime/executor.cc:1209] [/device:CPU:0] (DEBUG INFO) Executor start aborting (this does not indicate an error and you can ignore this message): INVALID_ARGUMENT: You mus

INFO:tensorflow:Assets written to: models/assets


INFO:tensorflow:Assets written to: models/assets
wandb: Adding directory to artifact (./models)... Done. 0.0s


2499/2499 [==============================] - 35s 14ms/step - loss: 0.0869 - categorical_accuracy: 0.9770 - auc: 0.9988 - precision: 0.9783 - recall: 0.9756 - val_loss: 0.0909 - val_categorical_accuracy: 0.9763 - val_auc: 0.9988 - val_precision: 0.9776 - val_recall: 0.9747
Epoch 16/100
1462/2499 [================>.............] - ETA: 8s - loss: 0.0843 - categorical_accuracy: 0.9782 - auc: 0.9988 - precision: 0.9795 - recall: 0.9769